# Visualize MRI Dist.
This notebook shows how to work with the data provided by MOINCC. Import packages

In [1]:
import polars as pl
import numpy as np
import matplotlib.pyplot as plt

Read data:

In [2]:
file_name = 'FA_20240206_2H_yeast_acetone-d6_3.csv'
file_path = '../Data/' + file_name
df = pl.read_csv(file_path) # using polars for more efficient data manipulation

Read in the Metadatafile:

In [3]:
import pandas as pd
pd.set_option('display.max_columns', None)
meta_path = '../Data/Data_description.xlsx'
meta_df = pd.read_excel(meta_path)
display(meta_df.head())

ID                                    File                  Expt_name  \
0   1   FA_20240206_2H_yeast_acetone-d6_3.csv   FA_20240206_2H_yeast_1_3   
1   2  FA_20240207_2H_yeast_Fumarate-d2_5.csv   FA_20240207_2H_yeast_1_5   
2   3  FA_20240213_2H_yeast_Fumarate-d2_9.csv  FA_20240213_2H_E.coli_1_9   
3   4  FA_20240228_2H_yeast_fumarate-d2_4.csv  FA_20240213_2H_E.coli_1_4   
4   5  FA_20240701_2H_yeast_fumarate-d2_8.csv   FA_20240701_2H_yeast_1_8   

   TR[s]  NS  TRtotal[s] Substrate_name Substrate_N_D  Substrate_mM  \
0   17.5   8         140     Acetone-d6             6            15   
1   11.5   8          92    Fumarate-d2           1,1            15   
2   11.5   8          92    Fumarate-d2           1,1            15   
3   11.5   8          92    Fumarate-d2           1,1            15   
4    2.5   8          20    Fumarate-d2           1,1            15   

  Substrate_ppm  pH_before  pH_after  Reaction temprature (Kelvin)  \
0         2.323        NaN      5.06                           310   
1         6.653        NaN      5.60                           310   
2         6.653        NaN      5.63                           310   
3         6.653        NaN      5.63                           310   
4         6.653        NaN      5.89                           310   

         Yeat_suspension Substrat_ solvent Substrate_mM_added  Water_ppm  \
0  1g yeast in 7mL water        PBS (50mM)               30mM        7.4   
1  1g yeast in 7mL water        PBS (50mM)               30mM        7.4   
2  1g yeast in 7mL water        PBS (50mM)               30mM        7.4   
3  1g yeast in 7mL water        PBS (50mM)               30mM        7.4   
4  1g yeast in 7mL water        PBS (50mM)               30mM        7.4   

     Metabolite_1  Metabolite_2  Metabolite_3  Metabolite_4  Metabolite_5  \
0  Propan-2-ol-d6           NaN           NaN           NaN           NaN   
1  Malate-d2(avg)           NaN           NaN           NaN           NaN   
2  Malate-d2(avg)           NaN           NaN           NaN           NaN   
3  Malate-d2(avg)           NaN           NaN           NaN           NaN   
4  Malate-d2(avg)           NaN           NaN           NaN           NaN   

  Metabolite_1_ppm  Metabolite_2_ppm  Metabolite_3_ppm  Metabolite_4_ppm  \
0            1.201               NaN               NaN               NaN   
1     4.368, 2.474               NaN               NaN               NaN   
2     4.368, 2.475               NaN               NaN               NaN   
3     4.368, 2.476               NaN               NaN               NaN   
4     4.368, 2.477               NaN               NaN               NaN   

  Metabolite_5_ppm  
0                -  
1              NaN  
2              NaN  
3              NaN  
4              NaN

Extract mentioned ppm values:

In [4]:
def extract_ppm_all(meta_df, file_name):
    meta_df = meta_df[meta_df['File'] == file_name]
    positions = []
    names = []
    # added substrat like acetone ppm
    react_substrat = str(meta_df['Substrate_ppm'].iloc[0]).split(',')
    for i in range(len(react_substrat)):
        names.append('ReacSubs')
        positions.append(float(react_substrat[i]))

    # add metabolite 1
    react_metabolite = str(meta_df['Metabolite_1_ppm'].iloc[0]).split(',')
    for i in range(len(react_metabolite)):
        names.append('Metab1')
        positions.append(float(react_metabolite[i]))

    # water ppm
    positions.append(float(meta_df['Water_ppm'].iloc[0]))
    names.append('Water')
    return positions, names

ppm_lines, names = extract_ppm_all(meta_df, file_name)




Plot of a single time point of the spectrum. You need to create a output folsder first! Inside this folder.^

In [8]:
def single_plot(df, y = 1, ppm_lines = ppm_lines, names = names):
    plt.figure(figsize=(10, 6))
    plt.plot(df[:, 0], df[:, y])
    plt.ylim(0, 70000)
    plt.xlabel('Chemical Shift (ppm)')
    plt.ylabel('Intensity')
    plt.title(f'NMR Spectrum of {file_name}')

    # make vertical lines for each ppm
    for i in range(len(ppm_lines)):
        plt.axvline(x=ppm_lines[i], color='r', linestyle='--', label='ppm')
        plt.text(ppm_lines[i], 7000, names[i], rotation=0)
    # save the plot
    plt.savefig(f'output/{file_name}_plot_{y}.png')
    # close figure
    plt.close()

for i in range(1,len(df.columns)):
    single_plot(df, i, ppm_lines, names=names)


Now create the gif:

In [15]:
from PIL import Image
import glob

# Create a GIF from the saved plots
def create_gif(file_name, output_dir='output', gif_name='nmr_spectrum.gif'):
    # Find all saved plot images (e.g., output/file_name_plot_1.png, output/file_name_plot_2.png, ...)
    image_files = glob.glob(f"{output_dir}/{file_name}_plot_*.png")

    # sort images by last number in file name
    image_files.sort(key=lambda x: int(x.split('_')[-1].split('.')[0]))
    

    print(image_files)
    
    # Open each image
    images = [Image.open(img) for img in image_files]
    
    # Save as GIF
    images[0].save(f"{output_dir}/{gif_name}", save_all=True, append_images=images[1:], duration=250, loop=0)
    
    print(f"GIF saved as {output_dir}/{gif_name}")

# Example usage
create_gif(file_name=file_name, output_dir='output', gif_name=f'nmr_spectrum_{file_name}.gif')


['output/FA_20240206_2H_yeast_acetone-d6_3.csv_plot_1.png', 'output/FA_20240206_2H_yeast_acetone-d6_3.csv_plot_2.png', 'output/FA_20240206_2H_yeast_acetone-d6_3.csv_plot_3.png', 'output/FA_20240206_2H_yeast_acetone-d6_3.csv_plot_4.png', 'output/FA_20240206_2H_yeast_acetone-d6_3.csv_plot_5.png', 'output/FA_20240206_2H_yeast_acetone-d6_3.csv_plot_6.png', 'output/FA_20240206_2H_yeast_acetone-d6_3.csv_plot_7.png', 'output/FA_20240206_2H_yeast_acetone-d6_3.csv_plot_8.png', 'output/FA_20240206_2H_yeast_acetone-d6_3.csv_plot_9.png', 'output/FA_20240206_2H_yeast_acetone-d6_3.csv_plot_10.png', 'output/FA_20240206_2H_yeast_acetone-d6_3.csv_plot_11.png', 'output/FA_20240206_2H_yeast_acetone-d6_3.csv_plot_12.png', 'output/FA_20240206_2H_yeast_acetone-d6_3.csv_plot_13.png', 'output/FA_20240206_2H_yeast_acetone-d6_3.csv_plot_14.png', 'output/FA_20240206_2H_yeast_acetone-d6_3.csv_plot_15.png', 'output/FA_20240206_2H_yeast_acetone-d6_3.csv_plot_16.png', 'output/FA_20240206_2H_yeast_acetone-d6_3.csv_pl

Now we want to vizualize the chemical shift over time:

In [7]:
import plotly.express as px
import polars as pl

def animate_plot(df):
    # Melt the dataframe (Polars)
    melted_df = df.melt(id_vars=[df.columns[0]], value_vars=df.columns[1:])
    display(melted_df)
    # Rename the columns for better understanding
    melted_df = melted_df.rename({
        df.columns[0]: 'Chemical Shift (ppm)',  # First column
        'variable': 'Time',  # The original column names (used as time points)
        'value': 'Intensity'  # The melted values (intensities)
    })
    
    # Convert the Polars DataFrame to a Pandas DataFrame for compatibility with Plotly
    melted_df = melted_df.to_pandas()

    # Create an animated line plot
    fig = px.line(
        melted_df,
        x='Chemical Shift (ppm)',  # x-axis
        y='Intensity',  # y-axis
        animation_frame='Time',  # Animation frames based on time (columns)
        labels={'Chemical Shift (ppm)': 'Chemical Shift (ppm)', "Intensity": "Intensity"},
        title="NMR Spectrum Animation"
    )

    # Update layout for better appearance
    fig.update_layout(
        xaxis_title="Chemical Shift (ppm)",
        yaxis_title="Intensity",
        width=800,
        height=500
    )
    
    # Show the animated plot
    fig.show()

# Example usage (assuming `df` is a Polars DataFrame)
animate_plot(df)


/tmp/ipykernel_655873/703580211.py:6: DeprecationWarning: `DataFrame.melt` is deprecated. Use `unpivot` instead, with `index` instead of `id_vars` and `on` instead of `value_vars`
  melted_df = df.melt(id_vars=[df.columns[0]], value_vars=df.columns[1:])


shape: (222_820, 3)
┌───────────────────┬─────────────────────────────────┬──────────┐
│ 2H chemical shift ┆ variable                        ┆ value    │
│ ---               ┆ ---                             ┆ ---      │
│ f64               ┆ str                             ┆ f64      │
╞═══════════════════╪═════════════════════════════════╪══════════╡
│ -0.879375         ┆ FA_20240206_2H_yeast_1.3.ser#1  ┆ -26.432  │
│ -0.875302         ┆ FA_20240206_2H_yeast_1.3.ser#1  ┆ 15.1197  │
│ -0.87123          ┆ FA_20240206_2H_yeast_1.3.ser#1  ┆ 56.6714  │
│ -0.867157         ┆ FA_20240206_2H_yeast_1.3.ser#1  ┆ 74.2474  │
│ -0.863085         ┆ FA_20240206_2H_yeast_1.3.ser#1  ┆ 91.8234  │
│ …                 ┆ …                               ┆ …        │
│ 6.08057           ┆ FA_20240206_2H_yeast_1.3.ser#1… ┆ 27.6844  │
│ 6.08464           ┆ FA_20240206_2H_yeast_1.3.ser#1… ┆ -38.4987 │
│ 6.08871           ┆ FA_20240206_2H_yeast_1.3.ser#1… ┆ -102.673 │
│ 6.09278           ┆ FA_20240206_2H_yeast_1.3.ser#1… ┆ -166.847 │
│ 6.09686           ┆ FA_20240206_2H_yeast_1.3.ser#1… ┆ -220.547 │
└───────────────────┴─────────────────────────────────┴──────────┘